# Filters and simple detections
Apply spatial filters and extract structure with edges, contours, and connected components.

In [ ]:
import cv2
import numpy as np
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D  # noqa: F401

%matplotlib inline

def load_demo_image(path="../images/sample.jpg"):
    image = cv2.imread(path)
    if image is None:
        gradient = np.linspace(0, 255, 256, dtype=np.uint8)
        image = np.dstack([gradient] * 3)
    return image

def show_gray(img, title):
    plt.imshow(img, cmap="gray")
    plt.title(title)
    plt.axis("off")

def plot3D(ax, img, title):
    x = np.flip(np.arange(img.shape[1]))
    y = np.arange(img.shape[0])
    X, Y = np.meshgrid(x, y)
    Z = img
    ax.plot_surface(X, Y, Z, cmap='gray', linewidth=0, antialiased=True)
    ax.set_title(title)
    ax.set_axis_off()

image = load_demo_image()
plt.figure(figsize=(8, 4))
plt.subplot(1, 2, 1)
show_gray(cv2.cvtColor(image, cv2.COLOR_BGR2GRAY), "imshow")
ax = plt.subplot(1, 2, 2, projection='3d')
ax.view_init(elev=70, azim=100, roll=0)
plot3D(ax, cv2.cvtColor(image, cv2.COLOR_BGR2GRAY), "3D Surface Plot")
plt.tight_layout()



## Noise reduction filters
Compare Gaussian and median filters for smoothing to reduce noise.

In [ ]:
def add_noise(image, noise_type="salt_and_pepper", amount=0.05, mean=0, var=0.01):
    noisy_image = image.copy()
    if noise_type == "salt_and_pepper":
        num_salt = np.ceil(amount * image.size * 0.5)
        coords = [np.random.randint(0, i - 1, int(num_salt)) for i in image.shape]
        noisy_image[coords[0], coords[1], :] = 255

        num_pepper = np.ceil(amount * image.size * 0.5)
        coords = [np.random.randint(0, i - 1, int(num_pepper)) for i in image.shape]
        noisy_image[coords[0], coords[1], :] = 0
    elif noise_type == "gaussian":
        scale_factor = 25
        if image.ndim == 3:
            row,col,ch = image.shape
            noise = scale_factor * np.random.normal(mean,var,(row,col,ch))
            noise = noise.reshape(row,col,ch)
        elif image.ndim == 2:
            row,col = image.shape
            noise = scale_factor * np.random.normal(mean,var,(row,col))
            noise = noise.reshape(row,col)
        noisy_image = np.uint8(np.clip((image + noise),0,255))
    return noisy_image

image = load_demo_image()

# choose one type of noise to add
#noisy_image = add_noise(image, noise_type="salt_and_pepper", amount=0.05)
noisy_image = add_noise(image, noise_type="gaussian", mean=0, var=1.0)

# Apply filters
k = 3
kernel_size = (k, k)
blur_gaussian = cv2.GaussianBlur(noisy_image, kernel_size, sigmaX=1.0)
blur_median = cv2.medianBlur(noisy_image, k)

plt.figure(figsize=(12, 4))

plt.subplot(1, 4, 1)
plt.imshow(cv2.cvtColor(image, cv2.COLOR_BGR2RGB))
plt.title("Original")
plt.axis("off")

plt.subplot(1, 4, 2)
plt.imshow(cv2.cvtColor(noisy_image, cv2.COLOR_BGR2RGB))
plt.title("Noisy")
plt.axis("off")

plt.subplot(1, 4, 3)
plt.imshow(cv2.cvtColor(blur_gaussian, cv2.COLOR_BGR2RGB))
plt.title(f"Gaussian {k}x{k}")
plt.axis("off")

plt.subplot(1, 4, 4)
plt.imshow(cv2.cvtColor(blur_median, cv2.COLOR_BGR2RGB))
plt.title(f"Median {k}x{k}")
plt.axis("off")
plt.tight_layout()


### Question
Which filter is more effective at reducing which kind of noise? Why? 

## Edge Detection
Use the Canny detector to find strong gradients. Tune thresholds to suit your image.

In [ ]:
image = load_demo_image()

gray = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
edges = cv2.Canny(gray, threshold1=50, threshold2=150)
show_gray(edges, "Canny edges")

### Question
How do the thresholds affect the detected edges? What happens if you apply Gaussian smoothing before edge detection?

## Contour Detection
Threshold the image and locate contours. Contours are handy for measuring shapes.

In [ ]:
image = load_demo_image(path="../images/screw.png")

gray = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
_, thresh = cv2.threshold(gray, 123, 255, cv2.THRESH_BINARY)
inv_thresh = cv2.bitwise_not(thresh)
contours, _ = cv2.findContours(inv_thresh, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)
contour_vis = image.copy()
cv2.drawContours(contour_vis, contours, -1, (0, 255, 0), 3)

plt.figure(figsize=(8, 4))
plt.subplot(1, 3, 1)
show_gray(thresh, "Threshold")
plt.subplot(1, 3, 2)
show_gray(inv_thresh, "Inverted Threshold")
plt.subplot(1, 3, 3)
plt.imshow(cv2.cvtColor(contour_vis, cv2.COLOR_BGR2RGB))
plt.title("Contours")
plt.axis("off")
plt.tight_layout()
print(f"Detected {len(contours)} contours")

### Question
Can you find a better threshold value that segments the screw more precisely?

## Morphological Operations
Use dilation and erosion to refine binary images.

In [ ]:
dilatation = cv2.dilate(inv_thresh, np.ones((3, 3), np.uint8), iterations=1)
erosion = cv2.erode(inv_thresh, np.ones((3, 3), np.uint8), iterations=1)

plt.figure(figsize=(8, 4))
plt.subplot(1, 3, 1)
show_gray(inv_thresh, "Original Threshold")
plt.subplot(1, 3, 2)
show_gray(dilatation, "Dilated Image")
plt.subplot(1, 3, 3)
show_gray(erosion, "Eroded Image")
plt.tight_layout()




## Connected Components
Label each region to compute statistics like area or bounding boxes.

In [ ]:
num_labels, labels, stats, centroids = cv2.connectedComponentsWithStats(dilatation, connectivity=8)
print(f"Components (including background): {num_labels}")

label_viz = np.zeros_like(image)
for label in range(1, num_labels): # do not color the background (label 0)
    mask = labels == label
    color = np.random.randint(0, 255, size=3, dtype=np.uint8)
    label_viz[mask] = color
    x, y, w, h, area = stats[label]
    cv2.rectangle(label_viz, (x, y), (x + w, y + h), (0, 255, 255), 1)

plt.figure(figsize=(6, 6))
plt.imshow(cv2.cvtColor(label_viz, cv2.COLOR_BGR2RGB))
plt.title("Connected components")
plt.axis("off")

## Task
Given a [color image of smarties](https://commons.wikimedia.org/wiki/File:Smarties_old_new.jpg), write code to count how many smarties are present using connected components analysis. Use an appropriate color space and thresholding method to segment the smarties from the background.

### Hint
As the smarties are of different colors, consider converting the image to HSV color space and thresholding based on saturation or value to separate them from the background. Note that the smarties may be touching each other, so you might need to apply morphological operations (like erosion and dilation) to separate them before applying connected components analysis. Note that this task is not easy to solve perfectly - I failed -, so focus on understanding the steps involved.